# "European Covid data exploration"
> "Exploring which countries have had the highest and lowest covid numbers in Europe"

- toc: true
- branch: master
- badges: true
- comments: false
- author: Ifan Johnston
- categories: [covid]

# Importing and preparing the data

We will be looking at data from the following countries:

- Italy
- Austria
- Germany
- Belgium
- France
- United Kingdom

We begin by importing the data, and adding calculating some new features so that we can compare the data from different countries. For example we calculate 'confirmed cases per 100k population', 'deaths per 100k' and 'new cases' since these are not initially in the dataset.

In [1]:
#collapse
from covid19dh import covid19
import altair as alt
import datetime

countries = ["Italy", 
             "Austria",
             "Germany",
             "Belgium",
             "France",
             "United Kingdom",
             "Switzerland"
            ]

yesterday = datetime.date.today() - datetime.timedelta(days=1)

x, src = covid19(countries, raw=True, verbose=False, end=yesterday, cache=False)

x_small = x.loc[:, ['administrative_area_level_1', 'date', 'vaccines', 'confirmed','tests', 'recovered', 'deaths', 'population']]
x_small.rename(columns={'administrative_area_level_1': 'id'}, inplace=True)

x_small['confirmed_per'] = 100000 * x_small['confirmed'] / x_small['population']
x_small['deaths_per'] = 100000 * x_small['deaths'] / x_small['population']
x_small['ratio'] = 100 * (x_small['deaths']) / (x_small['confirmed'])
x_small['tests_per'] = 100000 * (x_small['tests']) / (x_small['population'])
x_small['vaccines_per'] = x_small['vaccines'] / x_small['population']

x_small['new_cases']=x_small.groupby('id').confirmed.diff().fillna(0)
x_small['new_cases_per']=x_small.groupby('id').confirmed_per.diff().fillna(0)

Here is a random sample of 5 rows from the dataset.

In [2]:
x_small.tail()

id       date    vaccines  confirmed       tests  recovered  \
64758  Italy 2021-10-14  87110252.0  4709753.0  96364791.0  4498924.0   
64759  Italy 2021-10-15  87321575.0  4712482.0  96870834.0  4502457.0   
64760  Italy 2021-10-16  87488126.0  4715464.0  97343369.0  4505876.0   
64761  Italy 2021-10-17  87587669.0  4717899.0  97724420.0  4508789.0   
64762  Italy 2021-10-18  87770783.0  4719493.0  97944298.0  4511545.0   

         deaths  population  confirmed_per  deaths_per     ratio  \
64758  131461.0  60421760.0    7794.796113  217.572279  2.791250   
64759  131503.0  60421760.0    7799.312698  217.641790  2.790525   
64760  131517.0  60421760.0    7804.248006  217.664960  2.789057   
64761  131541.0  60421760.0    7808.278011  217.704681  2.788127   
64762  131585.0  60421760.0    7810.916134  217.777503  2.788117   

           tests_per  vaccines_per  new_cases  new_cases_per  
64758  159486.898429      1.441703     2666.0       4.412318  
64759  160324.416237      1.445201     2729.0       4.516585  
64760  161106.477203      1.447957     2982.0       4.935308  
64761  161737.129140      1.449605     2435.0       4.030005  
64762  162101.034462      1.452635     1594.0       2.638122

# Plotting the data

We will first look at the total numbers of cases and deaths in each country, before moving on to cases and deaths per 100k population.

{% include info.html text="In each of the charts below, you can click on the legend to filter the lines shown" %}

## Total cases per 100,000

In [3]:
#collapse

leg_selection = alt.selection_multi(fields=['id'], bind='legend')

alt.Chart(x_small).mark_line().encode(
    x=alt.X("yearmonthdate(date):T", axis=alt.Axis(title='Date')),
    y=alt.Y("confirmed_per:Q", axis=alt.Axis(title='Confirmed per 100k')),
    tooltip=['id', 'confirmed_per'],
    color=alt.Color('id', legend=alt.Legend(title="Countries")),
    opacity=alt.condition(leg_selection, alt.value(1), alt.value(0.2))
).add_selection(leg_selection).properties(title='Total number of cases per 100,000 population for selected European Countries', width=600).interactive()


alt.Chart(...)

## Total deaths per 100,000

In [4]:
#collapse
alt.Chart(x_small).mark_line().encode(
    x=alt.X("yearmonthdate(date):T", axis=alt.Axis(title='Date')),
    y=alt.Y("deaths_per:Q", axis=alt.Axis(title='Deaths per 100k')),
    tooltip='id',
    color=alt.Color('id', legend=alt.Legend(title="Countries")),
    opacity=alt.condition(leg_selection, alt.value(1), alt.value(0.2))
).add_selection(leg_selection).properties(title='Number of deaths per 100,000 population for selected European Countries', width=600).interactive()

alt.Chart(...)

## Two week incidence rate

In [5]:
#collapse
brush = alt.selection(type='interval', encodings=['x'])

base = alt.Chart(x_small).mark_line().transform_window(
    rolling_mean='sum(new_cases_per)',
    frame=[-7, 0],
    groupby=['id']
).encode(
    x=alt.X("yearmonthdate(date):T",
            axis=alt.Axis(title='Date')
           ),
    y=alt.Y("rolling_mean:Q",
            axis=alt.Axis(title='Incidence rate')
           ),
    tooltip=['id', 'rolling_mean:Q'],
    color=alt.Color('id', legend=alt.Legend(title="Countries")),
    opacity=alt.condition(leg_selection, alt.value(1), alt.value(0.2))
).add_selection(leg_selection).properties(
    width=600,
    height=400,
    title='Number of new cases per 100,000 over two weeks for selected countries'
)

upper = base.encode(
    alt.X('yearmonthdate(date):T',axis=alt.Axis(title='Date'),
          scale=alt.Scale(domain=brush))
)

lower = base.properties(
    height=60
).add_selection(brush)

upper & lower

alt.VConcatChart(...)

The ratio of confirmed cases and deaths gives an indication of what the case fatality rate is - it seems to be between 2 and 3%, assuming that the countries listed here are catching all positive cases (which they probably aren't, so it's likely lower than this).

## Case fatality rate

In [6]:
#collapse
base = alt.Chart(x_small).mark_line().encode(
    x=alt.X("yearmonthdate(date):T", axis=alt.Axis(title='Date')),
    y=alt.Y("ratio:Q", axis=alt.Axis(title='Ratio of deaths per case')),
    tooltip='id',
    color=alt.Color('id', legend=alt.Legend(title="Countries")),
opacity=alt.condition(leg_selection, alt.value(1), alt.value(0.2))
).add_selection(leg_selection).properties(title='The ratio of deaths to confirmed cases (case fatality rate)', width=600)

upper = base.encode(
    alt.X('yearmonthdate(date):T',axis=alt.Axis(title='Date'),
          scale=alt.Scale(domain=brush))
)

lower = base.properties(
    height=60
).add_selection(brush)

upper & lower

alt.VConcatChart(...)

# Vaccines

In the chart below we plot the number vaccines given per population - this means that if the number is 1, then the country has given the equivalent of 1 shot for each person in the country. Since not everyone in the countries are eligible to get the vaccine, a ratio of 1 means that many people have recieved two jabs. Note also that some kinds of vaccines (the J&J's [Janssen vaccine](https://www.cdc.gov/coronavirus/2019-ncov/vaccines/different-vaccines/janssen.html), for example) only require 1 shot so the goal is not neccesarily to reach exactly 2 shots per person in the whole country.

In [7]:
#collapse
alt.Chart(x_small.query("vaccines > 0")).mark_line().encode(
    x=alt.X("yearmonthdate(date):T", axis=alt.Axis(title='Date')),
    y=alt.Y("vaccines_per:Q", axis=alt.Axis(title='Number of vaccines given')),
    tooltip=['id', 'vaccines_per'],
    color=alt.Color('id', legend=alt.Legend(title="Countries")),
    opacity=alt.condition(leg_selection, alt.value(1), alt.value(0.2))
).add_selection(leg_selection).properties(title='Number of vaccines given', width=600).interactive()

alt.Chart(...)